# Setup

In [2]:
import torch.optim as optim
import torch.nn.functional as F
from torch.optim.lr_scheduler import ReduceLROnPlateau
import wandb
from utilities import *
from config import *
from dataloading import *
from tqdm import tqdm
from transformer import *
import os

In [4]:
(
        train_inputs, train_perms, train_dataloader, 
        val_seqs, val_perms, val_dataloader,
        test_seqs, test_perms, test_dataloader,
        dataset_size
) = load_data(skip_train=True)

KeyboardInterrupt: 

## Load model (accelerator version)

In [ ]:
from accelerate import Accelerator, load_checkpoint_and_dispatch
import os

# setup the model
model = Transformer()

accelerator = Accelerator()

#model = accelerator.prepare(model)

# optionally: load the model
save_directory = f"{PATH}/model/{MODELNAME}"
file_path = f"{save_directory}/model.safetensors"

if os.path.exists(file_path):
    model = load_checkpoint_and_dispatch(model, file_path)
    print("Loaded!")
else:
    print("Failed to load")

MODELNAME

Some weights of the model checkpoint at ./model/elem-partitioned-long-boosted-2/model.safetensors were not used when initializing Transformer: {'_orig_mod.blocks.1.ffwd.net.2.bias', '_orig_mod.blocks.4.ffwd.net.2.bias', '_orig_mod.blocks.0.sa.heads.4.value.weight', '_orig_mod.blocks.1.ln1.bias', '_orig_mod.blocks.2.ln1.weight', '_orig_mod.blocks.4.sa.heads.2.tril', '_orig_mod.blocks.4.sa.heads.0.key.weight', '_orig_mod.blocks.4.sa.heads.4.key.weight', '_orig_mod.blocks.3.ffwd.net.2.weight', '_orig_mod.blocks.3.sa.heads.5.query.weight', '_orig_mod.blocks.0.sa.heads.3.tril', '_orig_mod.blocks.4.ffwd.net.0.bias', '_orig_mod.blocks.1.ffwd.net.0.bias', '_orig_mod.blocks.4.sa.heads.3.key.weight', '_orig_mod.blocks.0.sa.heads.5.tril', '_orig_mod.blocks.1.sa.heads.5.query.weight', '_orig_mod.blocks.3.sa.heads.3.value.weight', '_orig_mod.blocks.2.sa.proj.bias', '_orig_mod.blocks.1.sa.proj.bias', '_orig_mod.blocks.3.sa.heads.4.key.weight', '_orig_mod.blocks.3.sa.heads.2.value.weight', '_orig_mod

Loaded!


'elem-partitioned-long-boosted-2'

In [3]:
vocab_size

652

In [4]:
model

Transformer(
  (token_embedding_table): Embedding(34, 402)
  (position_embedding): Embedding(136, 402)
  (embed_hook): Identity()
  (sa_heads): MultiHeadAttention(
    (heads): ModuleList(
      (0-5): 6 x Head(
        (key): Linear(in_features=402, out_features=67, bias=False)
        (query): Linear(in_features=402, out_features=67, bias=False)
        (value): Linear(in_features=402, out_features=67, bias=False)
        (dropout): Dropout(p=0, inplace=False)
        (attention_hook): Identity()
        (sanity_hook): Identity()
      )
    )
    (proj): Linear(in_features=402, out_features=402, bias=True)
    (dropout): Dropout(p=0, inplace=False)
  )
  (blocks): Sequential(
    (0): Block(
      (sa): MultiHeadAttention(
        (heads): ModuleList(
          (0-5): 6 x Head(
            (key): Linear(in_features=402, out_features=67, bias=False)
            (query): Linear(in_features=402, out_features=67, bias=False)
            (value): Linear(in_features=402, out_features=67, 

In [ ]:
sum(p.numel() for p in model.parameters() if p.requires_grad)

## Load model (legacy version)

In [ ]:
# setup the model
model = Transformer()

device = "cpu"
model = nn.DataParallel(model)
model = model.to(device)

# optionally: load the model
filename = f"{PATH}/model/{MODELNAME}.pth"

if os.path.isfile(filename):
    model.load_state_dict(torch.load(filename, map_location=torch.device(device)))

os.path.isfile(filename)
model = model.module

# Embedding pictures

In [20]:
import plotly.express as px
from math import sin, cos, tau

# generate embedding
embedding = []

period = 10
N = 2*period

for x in range(N):
    embedding.append(np.array([cos((tau*x)/period), sin((tau*x)/period)]))

similarity = []

for x in embedding:
    row = []
    for y in embedding:
        row.append(np.dot(x, y)/(np.linalg.norm(x)*np.linalg.norm(y)))
    similarity.append(row)

figure = px.imshow(similarity, title=f"Periodic embedding similarity matrix")
figure

In [3]:
import plotly.express as px

embedding = model.position_embedding(torch.arange(block_size)).detach().numpy()

similarity = []

for x in embedding:
    row = []
    for y in embedding:
        row.append(np.dot(x, y)/(np.linalg.norm(x)*np.linalg.norm(y)))
    similarity.append(row)

similarity = np.array(similarity)

figure = px.imshow(
    similarity,
    title=f"{MODELNAME} position embedding similarity matrix"
)

hide_ui = True

if hide_ui:
    figure.update_layout(coloraxis_showscale=True)
    figure.update_xaxes(showticklabels=False)
    figure.update_yaxes(showticklabels=False)
    figure.update_layout(
        title="",
        autosize=False,
        margin=dict(
            l=0,
            r=0,
            b=0,
            t=0,
            pad=0
        )
    )

figure

In [5]:
px.imshow(model.blocks[0].sa.heads[3].value.weight.detach().numpy())

In [ ]:
test_perms.apppend(list(range(16)))

In [7]:
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE

embedding = model.position_embedding(torch.arange(block_size)).detach().numpy()

pca = PCA(n_components=37)
pca_reduced = pca.fit_transform(embedding)

tsne = TSNE()
tsne_reduced = tsne.fit_transform(pca_reduced)

In [8]:
tsne_reduced

array([[-0.06686249, -2.7585614 ],
       [-0.04794812, -2.709017  ],
       [-0.03921476, -2.6321685 ],
       [-0.04373306, -2.5902817 ],
       [ 0.03546743, -2.226234  ],
       [-0.0235781 , -2.0767975 ],
       [-0.06743038, -1.9519619 ],
       [-0.19911835, -1.9161706 ],
       [-0.31126416, -2.0448413 ],
       [-0.425903  , -2.10752   ],
       [-0.4375873 , -2.3219383 ],
       [-0.6395197 , -2.2278037 ],
       [-0.8293289 , -2.1426864 ],
       [-0.88393563, -2.3014452 ],
       [-0.9218815 , -2.36688   ],
       [-0.8876559 , -2.578445  ],
       [-0.8096757 , -2.6369326 ],
       [-0.7250449 , -2.706064  ],
       [-0.6629079 , -2.7185168 ],
       [-0.5543748 , -2.8254313 ],
       [-0.5652758 , -2.8715734 ],
       [-0.61800456, -2.9613423 ],
       [-0.55387455, -3.029335  ],
       [-0.44811413, -3.1728172 ],
       [-0.26559418, -3.2966628 ],
       [ 0.06153211, -3.0905137 ],
       [-0.6524569 , -1.2245103 ],
       [-1.3168349 , -1.6214186 ],
       [ 0.4505259 ,

In [ ]:
import plotly.express as px

px.scatter(
    x=tsne_reduced[:,0], 
    y=tsne_reduced[:,1], 
    color=["input" for x in range(20)] + ["seperator"] + ["output" for x in range(16)]
)

In [ ]:
import wandb

wandb.login()
run = wandb.init()

In [ ]:
run.log({"image": wandb.Image(np.array(similarity))})

In [ ]:
plausible = 0

for perm in tqdm(test_perms):
    correct = 0

    for pos, char in enumerate(perm):
        if char == pos:
            correct += 1
    
    if correct >= 6:
        plausible += 1

plausible/len(test_perms)

In [ ]:
for x in test_dataloader:
    break

model(x[0][0].reshape((1,-1)))

In [ ]:
model(x[0][0].reshape((1,-1))).argsort(dim=1, descending=True)[0]

In [ ]:
test_perms[0]

In [ ]:
a.argmax()

In [ ]:
15+num_trans

In [ ]:
best = float("inf")

for perm in test_perms:
    fixed = 0

    for pos, char in enumerate(perm):
        fixed += pos == char
    
    best = min(fixed, best)

best

In [ ]:
vocab_size

In [8]:
import plotly.express as px

#embedding = model.token_embedding_table(torch.arange(vocab_size)).detach().cpu().numpy()
embedding = model.position_embedding(torch.arange(block_size)).detach().numpy()

similarity = []

for x in embedding:
    row = []
    for y in embedding:
        row.append(np.dot(x, y)/(np.linalg.norm(x)*np.linalg.norm(y)))
    similarity.append(row)

similarity = np.array(similarity)

figure = px.imshow(
    similarity,
    title=f"{MODELNAME} token embedding similarity matrix",
    #color_continuous_scale="YlOrRd_r",
    #zmin=similarity.min()-0.05,
    #zmin=-0.5,
    #zmax=0.3
)

hide_ui = True

if hide_ui:
    figure.layout["coloraxis"]["colorbar"].x = 0.5
    figure.layout["coloraxis"]["colorbar"].y = -0.1
    figure.layout["coloraxis"]["colorbar"].orientation = "h"
    #figure.update_xaxes(showticklabels=False)
    #figure.update_yaxes(showticklabels=False)
    figure.update_layout(
        title="",
        autosize=False,
        margin=dict(
            l=0,
            r=0,
            b=0,
            t=0,
            pad=0
        ),
        width=1000,
        height=1000
    )

figure

In [6]:
figure.write_image(f"./embedding_pictures/token/{MODELNAME}.png")

In [ ]:
embedding = model.token_embedding_table(torch.arange(vocab_size)).detach().cpu().numpy()

cov = []
mean = embedding.mean(axis=0)

for x in embedding:
    row = []
    for y in embedding:
        row.append(np.dot(x-mean, y-mean))
    cov.append(row)

cov = np.array(cov)
px.imshow(cov)

In [ ]:
eigs = np.linalg.eig(cov).eigenvalues
eigs.sort()
fig = px.bar(eigs[::-1])
fig.show()

In [ ]:
with open(f"./embedding_pictures/position/{MODELNAME}.npy", "wb") as file:
    np.save(file, similarity)

In [ ]:
with open(f"./embedding_pictures/position/{MODELNAME}.npy", "rb") as file:
    b = np.load(file)

b.shape

This next plot is found by taking the embeddings of $s_{i,j}$ at different positions and dotting them together (normed)

In [ ]:
def binarise(pos1, pos2, d=4):
    return torch.tensor([int(x) for x in format(2**(d)*pos1+pos2, f'#0{2*d+2}b')[2:]])

def process_tensor(tensor):
    return tensor.detach().numpy().reshape(-1)

similarity = []

digits = 5

for swap1 in range(2**(digits-1)):
    swap1_slice = []

    for swap2 in range(2**(digits-1)):
        swap2_slice = []

        for x in range(10):
            row = []

            for y in range(10):
                token_embedding = process_tensor(
                    model.token_embedding_table(binarise(swap1, swap2, digits))
                )

                vectors = []

                for j in (x, y):
                    position_embedding = process_tensor(
                        model.position_embedding(torch.arange(j*digits, (j+2)*digits))
                    )

                    swap_embedding = token_embedding + position_embedding
                    vectors.append(swap_embedding / np.linalg.norm(swap_embedding))
                
                row.append(np.dot(vectors[0], vectors[1]))
            swap2_slice.append(row)
        swap1_slice.append(swap2_slice)
    similarity.append(swap1_slice)

similarity = np.array(similarity)

In [ ]:
import plotly.graph_objects as go

# the following code is chatgpt generated (mostly)

def frame_name(i, j):
    return f"swap_{i}_{j}"

# Create initial heatmap (first slice)
initial_data = similarity[0, 0]
fig = go.Figure(data=go.Heatmap(z=initial_data))

zmin = np.min(similarity)
zmax = np.max(similarity)

# Define frames
frames = [
    go.Frame(
        data=go.Heatmap(z=similarity[i, j], zmin=zmin, zmax=zmax), 
        name=frame_name(i, j)
    )
    for i in range(similarity.shape[0])
    for j in range(similarity.shape[1])
]

# Add frames to the figure
fig.frames = frames

# Create slider steps for both sliders
slider1_steps = [
    {
        "args": [
            [frame_name(i, 0)],
            {
                "frame": {"duration": 300, "redraw": True},
                "mode": "immediate",
                "transition": {"duration": 300},
            },
        ],
        "label": f"Index {i}",
        "method": "animate",
    }
    for i in range(similarity.shape[0])
]

slider2_steps = [
    {
        "args": [
            [frame_name(0, j)],
            {
                "frame": {"duration": 300, "redraw": True},
                "mode": "immediate",
                "transition": {"duration": 300},
            },
        ],
        "label": f"Index {j}",
        "method": "animate",
    }
    for j in range(similarity.shape[1])
]

# Update layout with sliders
fig.update_layout(
    sliders=[
        {
            "currentvalue": {
                "font": {"size": 10},
                "prefix": "Tranposition 1: ",
                "visible": True,
                "xanchor": "center",
            },
            "steps": slider1_steps,
            "yanchor": "top",
            "xanchor": "left",
            "y": -0.1
        },
        {
            "currentvalue": {
                "font": {"size": 10},
                "prefix": "Transposition 2: ",
                "visible": True,
                "xanchor": "center",
            },
            "steps": slider2_steps,
            "yanchor": "top",
            "xanchor": "left",
            "y": -0.2
        }
    ],
    xaxis=dict(
        scaleanchor="y",
        scaleratio=1,
        constrain="domain"
    ),
    yaxis=dict(
        scaleanchor="x",
        scaleratio=1,
        constrain="domain"
    )
)

# Show the figure
fig.show()


In [10]:
vocab_size

34

In [ ]:
similarity = []

digits = 5

for swap in range(2**digits):
    swap_slice = []

    for kindex in range(MAX_TRANS_NUMBER):

        token_embedding = model.module.token_embedding_table(binarise(swap, swap+1, digits)).detach().numpy()

        matrices = []

        for j in (1, kindex):
            position_embedding = model.module.position_embedding(torch.arange(j*digits, (j+2)*digits)).detach().numpy()

            swap_embedding = token_embedding + position_embedding
            matrices.append(swap_embedding)

        swap_slice.append(np.dot(matrices[0], np.transpose(matrices[1])))
    
    similarity.append(swap_slice)

similarity = np.array(similarity)

In [ ]:
swap+1

In [ ]:
from plotly import optional_imports
nbformat = optional_imports.get_module("nbformat")
print(nbformat)

In [ ]:
import pandas as pd

results = pd.read_csv("./results/window-7.0.csv")

In [ ]:
num_results = results["results"].to_numpy().astype(int)

successes = []
failures = []

for perm, result in zip(test_perms, num_results):
    if result:
        successes.append(perm)
    else:
        failures.append(perm)

In [ ]:
results.head(10)

In [ ]:
val_perms[0]

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=3)

fit = pca.fit_transform(model.module.position_embedding(torch.arange(block_size)).detach().numpy())
fit

In [ ]:
pca.explained_variance_ratio_

In [ ]:
val_seqs[0]

# Custom ouput tests

In [25]:
# taken from https://web.stanford.edu/~nanbhas/blog/forward-hooks-pytorch/
# attach a bunch of interesting hooks
activation = {}
def get_activation(name):
    def hook(model, input, output):
        activation[name] = output.detach()
    return hook

model.embed_hook.register_forward_hook(get_activation("embed"))

if LEGACY_ARCHITECTURE:
    model.sa_heads.register_forward_hook(get_activation("sa_heads"))

    for pos, head in enumerate(model.sa_heads.heads):
        head.attention_hook.register_forward_hook(get_activation(f"sa_heads_{pos}"))
        head.sanity_hook.register_forward_hook(get_activation(f"sa_heads_{pos}_sanity"))

for x, block in enumerate(model.blocks[:-1]):
    if type(block) != Block:
        continue

    for y, head in enumerate(block.sa.heads):
        head.attention_hook.register_forward_hook(get_activation(f"block_{x}_head_{y}"))

    block.register_forward_hook(get_activation(f"block_{x}"))

model.lm_head.register_forward_hook(get_activation("lm_head"))

In [28]:
def get_perm_hybrid(seq, size):
    og = list(range(size))

    swaps = []

    for pos, x in enumerate(seq):
        if pos % 2 == 0:
            swaps.append([x])
        else:
            swaps[-1].append(x)
    
    for x, y in swaps:
        og[x], og[y] = og[y], og[x]

    return np.array(og)

def get_perm_elementary(seq, size):
    og = list(range(size))
    
    for x in seq:
        if x:
            og[x], og[x-1] = og[x-1], og[x]

    return np.array(og)

def convert_to_hybrid(seq, size):
    new = []
    
    for char in seq:
        new.append(int(char//size))
        new.append(int(char%size))
    
    return new

def convert_to_general(seq, size):
    new = []

    for x, y in zip(seq[::2], seq[1::2]):
        new.append(x*size + y)

    return new

custom = [1]
custom += [0 for x in range(INPUT_LENGTH-len(custom))]

true = get_perm_elementary(
    custom, 
    MAX_GROUP_SIZE
)

genned = model.generate(
    custom,
    accelerator,
    force_valid=True,
    debug=False,
    stop_at=float("inf") # early stopping for debug purposes
)

print("Real: ", true)
print("Model:", genned)
print("Same:", (true == genned).all())
print("Sortd:", np.sort(genned))

RuntimeError: Placeholder storage has not been allocated on MPS device!

In [ ]:
model.blocks[1].scale = 0

In [ ]:
activation["block_0"].flatten(start_dim=1).shape

In [ ]:
activation.keys()

In [15]:
import plotly.express as px
import numpy as np

# view the activation similarity matrices

def get_frame(name1, name2):
    # get the matrix
    layer1 = activation[name1].detach().numpy().squeeze()
    layer2 = activation[name2].detach().numpy().squeeze()

    normed1 = layer1/np.linalg.norm(layer1, axis=1, keepdims=True)
    normed2 = layer2/np.linalg.norm(layer2, axis=1, keepdims=True)

    return (normed1 @ normed2.transpose(-1,0))

px.imshow(get_frame("embed", "embed"), zmin=-1, zmax=1)

NameError: name 'activation' is not defined

In [ ]:
activation.keys()

In [ ]:
CONTEXT_LENGTH

In [53]:
# view attention
px.bar(activation["lm_head"].detach().numpy().squeeze()[-1])#), zmin=0, zmax=1)

In [60]:
px.imshow(activation["block_4_head_5"].detach().numpy().squeeze())#, zmin=0, zmax=1)

In [ ]:
activation["block-4"][0].shape

In [ ]:
activation["block-4"][0] @ model.lm_head.weight[0]

In [63]:
weight1 = model.blocks[4].sa.heads[0].query.weight.detach().numpy().squeeze()
weight2 = model.blocks[4].sa.heads[0].key.weight.detach().numpy().squeeze()

normed1 = weight1/np.linalg.norm(weight1, axis=1, keepdims=True)
normed2 = weight2/np.linalg.norm(weight2, axis=1, keepdims=True)

cov = (weight1.transpose(-1,0) @ weight2)
px.imshow(cov)

In [86]:
np.linalg.norm(weight1.transpose(-1,0) @ weight2, ord="fro")

79.22581

In [64]:
cov = (weight1 @ weight2.transpose(-1,0))
px.imshow(cov)

In [ ]:
cov = (weight1.transpose(-1,0) @ weight2)
px.imshow(cov)

In [83]:
model.blocks[0].sa.heads[0].value.weight.detach().numpy()

array([[-0.00127411,  0.00668335,  0.00028992, ...,  0.00283813,
         0.00098419, -0.00078583],
       [-0.00241089, -0.00210571,  0.00515747, ...,  0.00338745,
         0.0019455 , -0.00717163],
       [-0.00093079,  0.00405884, -0.00171661, ..., -0.00053787,
         0.00016689, -0.00049591],
       ...,
       [-0.00361633, -0.00393677,  0.00331116, ..., -0.00189209,
         0.00039291, -0.00695801],
       [-0.00389099,  0.00267029,  0.00552368, ..., -0.00061798,
        -0.00132751,  0.00101471],
       [-0.00195312, -0.00091171,  0.00268555, ..., -0.00043869,
        -0.00367737, -0.00389099]], dtype=float32)

In [80]:
CONTEXT_LENGTH

46

In [66]:
px.imshow(model.blocks[4].sa.heads[0].key.weight.detach().numpy())

In [67]:
np.linalg.matrix_rank(model.blocks[0].sa.heads[0].query.weight.detach().numpy(), tol=10**-3)

67

In [68]:
px.bar(np.linalg.svd(model.blocks[0].sa.heads[0].key.weight.detach().numpy()).S)

In [69]:
px.bar(np.linalg.svd(cov).S)

In [70]:
np.linalg.matrix_rank(cov)

67

In [ ]:
# view the lm_head weight covariance matrix

weight = model.lm_head.weight.detach().numpy().squeeze()
normed = weight/np.linalg.norm(weight, axis=1, keepdims=True)
cov = (normed @ normed.transpose(-1,0))
px.imshow(cov, zmin=-1, zmax=1)

In [ ]:
model.position_embedding(torch.arange(CONTEXT_LENGTH)).shape

In [ ]:
a = np.array([[1,1],[-1,-1]])
a.mean(axis=1)

In [ ]:
a = range(20)

for x, y in zip(a[::2], a[1::2]):
    print(x, y)

In [ ]:
convert_to_general(custom, 16)

In [ ]:
[0 for x in range(20)]

In [ ]:
# wrong
b = torch.tensor([-265.7672, -265.7672, -265.7672, -265.7672, -265.7672, -265.7672,
         -265.7672, -265.7672, -265.7672, -265.7672, -265.7672, -265.7672,
         -265.7672, -265.7672, -265.7672, -265.7672, -240.0325, -247.6589,
         -246.5491, -257.4102, -257.1504, -257.8494, -255.2135, -254.7709,
         -253.9813, -256.4985, -256.2157, -261.1152, -266.6082, -258.3374,
         -273.0349, -261.6855, -265.7672, -265.7672])

import plotly.express as px
px.bar(b[16:32]-b[16:32].max()-1)

In [ ]:
train_perms[0]

In [ ]:
success_fixed_count = []

for perm in successes:
    fixed_count = 0

    for pos, char in enumerate(perm):
        if pos == char:
            fixed_count += 1
    
    success_fixed_count.append(fixed_count)

sum(success_fixed_count)/len(success_fixed_count)

In [ ]:
failure_fixed_count = []

for perm in failures:
    fixed_count = 0

    for pos, char in enumerate(perm):
        if pos == char:
            fixed_count += 1
    
    failure_fixed_count.append(fixed_count)

sum(failure_fixed_count)/len(failure_fixed_count)

In [ ]:
import csv

with open('win-7-succs.csv', 'w', newline='') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(["successes"])

    for x in success_fixed_count:
        writer.writerow([x])


In [ ]:
import csv

with open('win-7-fails.csv', 'w', newline='') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(["failures"])

    for x in failure_fixed_count:
        writer.writerow([x])

In [ ]:
from importlib import import_module

In [ ]:
import_module("nbformat")

In [ ]:
import nbformat

In [ ]:
!pip uninstall rpds-py

In [ ]:
!pip show nbformat

In [ ]:
!pip install --upgrade notebook jupyter jupyterlab

In [ ]:
!pip install --upgrade plotly

In [ ]:
00110100

In [ ]:
convert_tokens_to_perm([12,13,14,15,16,17])

In [ ]:
k = 0
seq = val_seqs[k]
perm = val_perms[k]
perm

In [ ]:
a = model.module.generate(seq)

In [ ]:
# Calculate and print accuracy after each epoch
with torch.no_grad():
    model.eval()  # Set the model to evaluation mode

    # calculate validation stats
    total_accuracy = 0.0
    total_loss = 0.0

    num_batches = 0

    print("Evaluating...")
    for inputs, targets in tqdm(val_dataloader):
        outputs = model(inputs)

        0/0

        # calculate the val accuracy
        accuracy = calculate_accuracy(outputs, targets)
        total_accuracy += accuracy

        # Calculate the val loss
        loss = criterion(outputs, targets)
        total_loss += loss.item()
        num_batches += 1

    average_accuracy = total_accuracy / num_batches
    val_loss = total_loss / num_batches

    metrics = {
        "validation_accuracy": average_accuracy,
        "loss": val_loss,
        "training_accuracy": average_train_accuracy,
        "training_loss": train_loss,
    }

In [ ]:
inputs[2]

In [ ]:
outputs[2]

In [ ]:
torch.argmax(outputs[2])

In [ ]:
model.module.softmax(outputs)[1]

In [ ]:
targets[1]

In [ ]:
val_perms[0]

In [ ]:
import pyperclip

def np_to_mathematica(array, copy=True):
    formatted = str(array.tolist()).replace("[", "{").replace("]", "}")
    return formatted

In [ ]:
pyperclip.copy(np_to_mathematica(embedding_pca))
print("Copied!")

In [ ]:
from sklearn.decomposition import PCA
import numpy as np

embedding = np.array(model.module.token_embedding_table.weight.cpu().detach().numpy())
pos_embedding = np.array(model.module.position_embedding.weight.cpu().detach().numpy())

pca = PCA(n_components=3)
pca.fit(embedding)

embedding_pca = pca.transform(embedding)

pca = PCA(n_components=2)
pca.fit(pos_embedding)

pos_embedding_pca = pca.transform(pos_embedding)

In [ ]:
import plotly.express as px

similarity = []

for x in embedding:
    row = []
    for y in embedding:
        row.append(np.dot(x, y))
    similarity.append(row)

px.imshow(similarity)

In [ ]:
np.dot(pos_embedding[MAX_LENGTH], embedding[START_PREDICTION_TOKEN])

In [ ]:
threshold = 30

for pos1, x in enumerate(embedding):
    for pos2, y in enumerate(embedding):
        if np.dot(x, y) > threshold and pos1 != pos2:
            print("x", pos1, "y", pos2, "dot", np.dot(x, y))

In [ ]:
px.imshow(model.module.token_embedding_table.weight.detach())

In [ ]:
torch.no_grad()
model.eval()

In [ ]:
targets

In [ ]:
# calculate validation stats
criterion = nn.CrossEntropyLoss()

total_accuracy = 0.0
total_loss = 0.0

num_batches = 0

print("Evaluating...")
for inputs, targets in tqdm(val_dataloader):
    outputs = model(inputs)

    # calculate the val accuracy
    accuracy = calculate_accuracy(outputs, targets)
    total_accuracy += accuracy

    # Calculate the val loss
    loss = criterion(outputs, targets)
    total_loss += loss.item()
    num_batches += 1

average_accuracy = total_accuracy / num_batches
val_loss = total_loss / num_batches

In [ ]:
val_loss

In [ ]:
vocab_size

In [ ]:
output = model(data)

In [ ]:
train

In [ ]:
train.shape

In [ ]:
output.shape

In [ ]:
output[1]

In [ ]:
model.get_device()

In [ ]:
dev

In [ ]:
if cuda.is_available():
    dev = "cuda:0"
else:
    dev = "cpu"

In [ ]:
conver

In [ ]:
model.eval()

# use gpu for processing
if cuda.is_available():
    dev = "cuda:0"
else:
    dev = "cpu"

# create an initial input
input_tensor = torch.ones(block_size, dtype=int).to(dev)
input_tensor *= TO_PREDICT_TOKEN
input_tensor[:len(seq)] = torch.tensor(seq, dtype=int).to(dev)
input_tensor[len(seq)] = START_PREDICTION_TOKEN

In [ ]:
input_tensor.unsqueeze(0)

In [ ]:
model(input_tensor.unsqueeze(0))

In [ ]:
torch.argmax(model(input_tensor.unsqueeze(0)), dim=1)

In [ ]:
prediction_tensor = torch.zeros(block_size, dtype=int).to(dev)

In [ ]:
sequence = [1,2,3,1,2,3]

In [ ]:
prediction_tensor[:len(sequence)] = torch.tensor(sequence, dtype=int).to(dev)

In [ ]:
prediction_tensor

In [ ]:
input_tensor = torch.ones(block_size, dtype=int).to(dev)

In [ ]:
input_tensor *= TO_PREDICT_TOKEN

In [ ]:
input_tensor

# Probes test

In [ ]:
from probed_transfomer import ProbedTransformer

# setup the model
probed_model = ProbedTransformer(stop_block=1)

device = "cpu"
probed_model = nn.DataParallel(probed_model)
probed_model = probed_model.to(device)

# optionally: load the model
filename = f"{PATH}/model/{MODELNAME}.pth"

if os.path.isfile(filename):
    probed_model.load_state_dict(torch.load(filename, map_location=torch.device(device)), strict=False)

os.path.isfile(filename)
probed_model = probed_model.module

In [ ]:
probed_model.blocks[1].classifier.weight

In [ ]:
probed_model.blocks[0].ffwd.net[0].weight.requires_grad

In [ ]:
probed_model.probe.classifier.weight

In [ ]:
# accelerate version
from accelerate import Accelerator, load_checkpoint_and_dispatch
from probed_transfomer import ProbedTransformer

# setup the model
probed_model = ProbedTransformer()

accelerator = Accelerator()

# optionally: load the model
save_directory = f"{PATH}/model/{MODELNAME}-probed"
file_path = f"{save_directory}/model.safetensors"

probed_model = load_checkpoint_and_dispatch(probed_model, file_path)

In [ ]:
# add intervention
class Intervention(nn.Module):
    def __init__(self, addition, scale):
        super().__init__()
        
        self.addition = addition
        self.scale = scale
    
    def forward(self, x):
        flat_x = x.flatten(start_dim=1)
        coefficient = self.scale*((flat_x @ self.addition)/self.addition.norm())
        return x + coefficient*self.addition.reshape(x.shape)

In [ ]:
# inject intervention into model

injection_spot = 1
scale = 1

intervention = Intervention(probed_model.probe.classifier.weight[0], scale)

model.blocks.insert(injection_spot, intervention)

# pretty pictures

In [ ]:
with open("./embedding_pictures/position/torn-1.0.npy", "rb") as file:
    pos_pictures = np.load(file)

with open("./embedding_pictures/token/torn-1.0.npy", "rb") as file:
    token_pictures = np.load(file)

In [ ]:
def show_image(image):
    return px.imshow(
        image, 
        animation_frame=0, 
        zmin=image.min(),
        zmax=image.max()
    )

show_image(token_pictures)

# Weight matrix eigenvalues

In [ ]:
model.blocks[0].ffwd

In [ ]:
len(model.blocks)

In [ ]:
linear = model.blocks[0].ffwd.net[0]
weights = linear.weight.detach().numpy()
fig = px.bar(np.linalg.svd(weights).S)
fig.show()

In [ ]:
linear = model.blocks[0].ffwd.net[2]
weights = linear.weight.detach().numpy()
fig = px.bar(np.linalg.svd(weights).S)
fig.show()

In [ ]:
linear = model.module.blocks[0].ffwd.net[0]
weights = linear.weight.detach().numpy()
np.linalg.svd(weights).U[:,0]

In [ ]:
linear = model.module.blocks[1].ffwd.net[0]
weights = linear.weight.detach().numpy()
np.linalg.svd(weights).U[:,0]

In [ ]:
model.module.blocks[0].ffwd

# Fixing the loss

In [4]:
for inputs, targets in val_dataloader:
    xb = inputs
    yb = targets
    break

In [5]:
xb.shape

torch.Size([2, 136])

In [6]:
yb.shape

torch.Size([2, 16])

In [7]:
logits = model(xb)
logits.shape

torch.Size([2, 16, 34])

In [10]:
CONTEXT_LENGTH

50

In [34]:
lmao = logits[:, MAX_GROUP_SIZE:, :]
B, T, C = lmao.shape

In [35]:
B,T,C

(1024, 25, 652)

In [29]:
lmao.reshape(B*T, C).shape

torch.Size([25600, 652])

In [22]:
lmao[0]

tensor([[ 0.8637, -0.2799,  0.4006,  ...,  0.0406, -0.3273,  0.5003],
        [ 0.8543, -0.2757,  0.4046,  ...,  0.0505, -0.3065,  0.5092],
        [ 0.8773, -0.2865,  0.3671,  ...,  0.0499, -0.3134,  0.4498],
        ...,
        [ 0.8733, -0.2402,  0.4031,  ...,  0.0515, -0.2808,  0.4922],
        [ 0.8804, -0.2522,  0.4237,  ...,  0.0625, -0.2308,  0.4796],
        [ 0.8654, -0.2762,  0.4007,  ...,  0.0761, -0.3098,  0.5011]],
       grad_fn=<SelectBackward0>)

In [31]:
inputs[:, MAX_GROUP_SIZE:].reshape(B*T).shape

torch.Size([25600])

In [33]:
from torch.nn import functional as F

F.cross_entropy(lmao.reshape(B*T, C), inputs[:, MAX_GROUP_SIZE:].reshape(B*T))

tensor(6.5980, grad_fn=<NllLossBackward0>)

In [13]:
targets.shape

torch.Size([1024, 24])

In [16]:
len([389, 254,  10, 121, 157, 354, 615, 549, 615, 354, 604, 182, 174, 600,
        265, 621, 374, 254,  21, 514, 199, 350, 274, 150,  24])

25

In [5]:
inputs.shape

torch.Size([1024, 49])

In [13]:
torch.tril(torch.ones(10, 10), 0)

tensor([[1., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
        [1., 1., 0., 0., 0., 0., 0., 0., 0., 0.],
        [1., 1., 1., 0., 0., 0., 0., 0., 0., 0.],
        [1., 1., 1., 1., 0., 0., 0., 0., 0., 0.],
        [1., 1., 1., 1., 1., 0., 0., 0., 0., 0.],
        [1., 1., 1., 1., 1., 1., 0., 0., 0., 0.],
        [1., 1., 1., 1., 1., 1., 1., 0., 0., 0.],
        [1., 1., 1., 1., 1., 1., 1., 1., 0., 0.],
        [1., 1., 1., 1., 1., 1., 1., 1., 1., 0.],
        [1., 1., 1., 1., 1., 1., 1., 1., 1., 1.]])

In [9]:
INPUT_LENGTH = 5
CONTEXT_LENGTH = INPUT_LENGTH + 10

noninputlength = CONTEXT_LENGTH-INPUT_LENGTH
A = torch.ones(INPUT_LENGTH, INPUT_LENGTH)
B = torch.zeros(INPUT_LENGTH, noninputlength)
C = torch.ones(noninputlength, INPUT_LENGTH)
D = torch.tril(torch.ones(noninputlength, noninputlength))

E = torch.cat((torch.cat((A, B), dim=1), torch.cat((C, D), dim=1)), dim=0)

In [12]:
E.shape

torch.Size([15, 15])

In [32]:
repr(D)

'tensor([[1., 1., 1.,  ..., 1., 1., 1.],\n        [1., 1., 1.,  ..., 1., 1., 1.],\n        [1., 1., 1.,  ..., 1., 1., 1.],\n        ...,\n        [1., 1., 1.,  ..., 1., 0., 0.],\n        [1., 1., 1.,  ..., 1., 1., 0.],\n        [1., 1., 1.,  ..., 1., 1., 1.]])'

# Spooky scary inverse functions

In [31]:
# finds the reduced word for a given permutation
# uses adjacent transpositions
# output is a series of tokens representing the word
# 1 means s_{0,1}, 2 means s_{1,2}, etc.
def permutation_reverse(permutation):
    if sorted(permutation) != list(range(len(permutation))):
        raise Exception("Permutation is invalid")

    word = []
    current_state = list(range(len(permutation)))
    for goal, item in enumerate(permutation):
        cur_loc = current_state.index(item)

        if cur_loc == goal:
            continue
        elif cur_loc > goal:
            word += list(range(goal+1, cur_loc+1))[::-1]
        else:
            word += list(range(cur_loc+1, goal+1))

        current_state.insert(goal, current_state.pop(cur_loc))

    return word

permutation_reverse([3,4,1,0,5,2])

[3, 2, 1, 4, 3, 2, 3, 5]

In [40]:
for perm in test_perms:
    assert((perm == get_perm_elementary(permutation_reverse(perm), MAX_GROUP_SIZE)).all())

In [16]:
a = list(range(1,7))
a.insert(0, a.pop(3))
a.insert(1, a.pop(4))
a.insert(2, a.pop(3))
a.insert(5, a.pop(4))
a

[4, 5, 2, 1, 6, 3]